In [15]:
import faulthandler
faulthandler.enable()
# Import the game
import gym_super_mario_bros
# Import the Joypad wrapper
from nes_py.wrappers import JoypadSpace
# Import the SIMPLIFIED controls
from gym_super_mario_bros.actions import SIMPLE_MOVEMENT
import gym

# 2. Preprocess Environment

In [16]:
# Import Frame Stacker Wrapper and GrayScaling Wrapper
from gym.wrappers import GrayScaleObservation
# Import Vectorization Wrappers
from stable_baselines3.common.vec_env import VecFrameStack, DummyVecEnv
# Import Matplotlib to show the impact of frame stacking
from matplotlib import pyplot as plt

In [17]:
# 1. Create the base environment
env = gym.make('SuperMarioBros-v0', apply_api_compatibility=True, render_mode="human")
# 2. Simplify the controls 
JoypadSpace.reset = lambda self, **kwargs: self.env.reset(**kwargs)
env = JoypadSpace(env, SIMPLE_MOVEMENT)
# 3. Grayscale
env = GrayScaleObservation(env, keep_dim=True)
# 4. Wrap inside the Dummy Environment
env = DummyVecEnv([lambda: env])
# 5. Stack the frames
env = VecFrameStack(env, 4, channels_order='last')

# 3. Train the RL Model

In [18]:
# Import os for file path management
import os 
# Import PPO for algos
from stable_baselines3 import PPO
# Import Base Callback for saving models
from stable_baselines3.common.callbacks import BaseCallback

In [19]:
import datetime
class TrainAndLoggingCallback(BaseCallback):

    def __init__(self, check_freq, save_path, verbose=1):
        super(TrainAndLoggingCallback, self).__init__(verbose)
        self.check_freq = check_freq
        self.save_path = save_path

    def _init_callback(self):
        if self.save_path is not None:
            os.makedirs(self.save_path, exist_ok=True)

    def _on_step(self):
        if self.n_calls % self.check_freq == 0:
            model_path = os.path.join(self.save_path, 'best_model_{}_{}.zip'.format(datetime.datetime.now(), self.n_calls))
            self.model.save(model_path)

        return True

In [20]:
CHECKPOINT_DIR = './train/'
LOG_DIR = './logs/'

In [21]:
# Setup model saving callback
callback = TrainAndLoggingCallback(check_freq=10000, save_path=CHECKPOINT_DIR)

In [22]:
# This is the AI model started
model = PPO('CnnPolicy', env, verbose=1, tensorboard_log=LOG_DIR, learning_rate=0.000001, 
            n_steps=512) 

import glob
import os

list_of_files = glob.glob('./train/*')
latest_file = max(list_of_files, key=os.path.getctime)
# Get latest model file from ./train folder and load it into the model
model.load(latest_file) 

Using cuda device
Wrapping the env in a VecTransposeImage.


/home/kunal7906/.local/lib/python3.10/site-packages/stable_baselines3/common/save_util.py:167: UserWarning: Could not deserialize object observation_space. Consider using `custom_objects` argument to replace this object.
Exception: __generator_ctor() takes from 0 to 1 positional arguments but 2 were given
  warnings.warn(
/home/kunal7906/.local/lib/python3.10/site-packages/stable_baselines3/common/save_util.py:167: UserWarning: Could not deserialize object clip_range. Consider using `custom_objects` argument to replace this object.
Exception: Can't get attribute '_function_setstate' on <module 'cloudpickle.cloudpickle' from '/home/kunal7906/.local/lib/python3.10/site-packages/cloudpickle/cloudpickle.py'>
  warnings.warn(
/home/kunal7906/.local/lib/python3.10/site-packages/stable_baselines3/common/save_util.py:167: UserWarning: Could not deserialize object lr_schedule. Consider using `custom_objects` argument to replace this object.
Exception: Can't get attribute '_function_setstate' on

KeyError: "The observation_space and action_space were not given, can't verify new environments"

In [9]:
# Train the AI model, this is where the AI model starts to learn
model.learn(total_timesteps=3000000, callback=callback)

Logging to ./logs/PPO_23


/home/kunal-pal/.local/lib/python3.10/site-packages/gym/utils/passive_env_checker.py:233: DeprecationWarning: `np.bool8` is a deprecated alias for `np.bool_`.  (Deprecated NumPy 1.24)
  if not isinstance(terminated, (bool, np.bool8)):
/home/kunal-pal/.local/lib/python3.10/site-packages/gym_super_mario_bros/smb_env.py:148: RuntimeWarning: overflow encountered in scalar subtract
  return (self.ram[0x86] - self.ram[0x071c]) % 256


----------------------------
| time/              |     |
|    fps             | 73  |
|    iterations      | 1   |
|    time_elapsed    | 6   |
|    total_timesteps | 512 |
----------------------------
-------------------------------------------
| time/                   |               |
|    fps                  | 70            |
|    iterations           | 2             |
|    time_elapsed         | 14            |
|    total_timesteps      | 1024          |
| train/                  |               |
|    approx_kl            | 0.00010216015 |
|    clip_fraction        | 0             |
|    clip_range           | 0.2           |
|    entropy_loss         | -1.95         |
|    explained_variance   | -0.00173      |
|    learning_rate        | 1e-06         |
|    loss                 | 144           |
|    n_updates            | 10            |
|    policy_gradient_loss | -0.000227     |
|    value_loss           | 377           |
-------------------------------------------
-----

In [10]:
model.save('thisisatestmodel')

# 4. Test it Out

In [23]:
# Load model
list_of_files = glob.glob('./train/*')
latest_file = max(list_of_files, key=os.path.getctime)
model = PPO.load(latest_file)

KeyError: "The observation_space and action_space were not given, can't verify new environments"

In [24]:
state = env.reset()

In [ ]:
# Start the game 
state = env.reset()
# Loop through the game
while True: 
    
    action, _ = model.predict(state)
    state, reward, done, info = env.step(action)
    env.render()

/home/kunal7906/.local/lib/python3.10/site-packages/gym/utils/passive_env_checker.py:272: UserWarning: WARN: No render modes was declared in the environment (env.metadata['render_modes'] is None or not defined), you may have trouble when calling `.render()`.
  logger.warn(


In [7]:
env.close()